# Introduction

This notebook explores [Zipf's law](https://en.wikipedia.org/wiki/Zipf%27s_law) using the [Wikitext-103 dataset](https://blog.einstein.ai/the-wikitext-long-term-dependency-language-modeling-dataset/).

# Setup

Install some libraries:

In [1]:
%%capture
!conda install -y -c conda-forge spacy
!pip install plotly
!python -m spacy download en

Navigate to the projects root folder:

In [2]:
%cd ..

/home/jovyan/work


# Libraries

In [3]:
import pandas as pd
import numpy as np

import plotly.offline as py
import plotly.figure_factory as ff
import plotly.graph_objs as go

import plotly
plotly.offline.init_notebook_mode(connected=True)

import spacy
import collections

import scipy

# Data

Download the wikitext-103 dataset:

In [4]:
!wget --continue --directory-prefix=./data https://s3.amazonaws.com/research.metamind.io/wikitext/wikitext-103-raw-v1.zip
!unzip -n ./data/wikitext-103-raw-v1.zip -d ./data

--2019-03-10 09:06:57--  https://s3.amazonaws.com/research.metamind.io/wikitext/wikitext-103-raw-v1.zip
Resolving s3.amazonaws.com (s3.amazonaws.com)... 52.216.101.165
Connecting to s3.amazonaws.com (s3.amazonaws.com)|52.216.101.165|:443... connected.
HTTP request sent, awaiting response... 416 Requested Range Not Satisfiable

    The file is already fully retrieved; nothing to do.

Archive:  ./data/wikitext-103-raw-v1.zip


# Explore

List available files in the extracted zip file:

In [5]:
%ls -la ./data/wikitext-103-raw/

total 530292
drwxrwxrwx 1 jovyan staff      4096 Sep 27  2016 ./
drwxrwxrwx 1 jovyan staff      4096 Mar  9 15:42 ../
-rwxrwxrwx 1 jovyan staff   1290590 Aug  4  2016 wiki.test.raw*
-rwxrwxrwx 1 jovyan staff 540568191 Aug  4  2016 wiki.train.raw*
-rwxrwxrwx 1 jovyan staff   1146846 Aug  4  2016 wiki.valid.raw*


In [6]:
input_file = './data/wikitext-103-raw/wiki.test.raw'

View some examples in the corpus:

In [7]:
!head -n 20 {input_file}

 
 = Robert Boulter = 
 
 Robert Boulter is an English film , television and theatre actor . He had a guest @-@ starring role on the television series The Bill in 2000 . This was followed by a starring role in the play Herons written by Simon Stephens , which was performed in 2001 at the Royal Court Theatre . He had a guest role in the television series Judge John Deed in 2002 . In 2004 Boulter landed a role as " Craig " in the episode " Teddy 's Story " of the television series The Long Firm ; he starred alongside actors Mark Strong and Derek Jacobi . He was cast in the 2005 theatre productions of the Philip Ridley play Mercury Fur , which was performed at the Drum Theatre in Plymouth and the Menier Chocolate Factory in London . He was directed by John Tiffany and starred alongside Ben Whishaw , Shane Zaza , Harry Kent , Fraser Ayres , Sophie Stanton and Dominic Hall . 
 In 2006 , Boulter starred alongside Whishaw in the play Citizenship written by Mark Ravenhill . He appeared on a 20

A pipeline component to ignore certain tokens:

In [8]:
class TokenKeeper:
    name='the_token_ignorer'
    def __init__(self, blacklist_tokens=[]):
        self.blacklist_tokens=blacklist_tokens
        spacy.tokens.Token.set_extension('is_ignored', default=False, force=True)
    
    def __call__(self, doc):
        for token in doc:
            if not token.is_alpha or token.text in self.blacklist_tokens:
                token._.set('is_ignored', True)
        
        return doc

In [9]:
nlp = spacy.load('en')
nlp.add_pipe(TokenKeeper(), first=True)

For each line in the dataset, track the frequency of each tokens:

In [10]:
%%time
counter = collections.Counter()

with open(input_file) as f:
    for line in f:
        doc = nlp(line)
        for token in doc:
            if not token._.is_ignored:
                counter[token.lower_] = counter[token.lower_] + 1

CPU times: user 1min 55s, sys: 283 ms, total: 1min 56s
Wall time: 1min 56s


Convert the counter into a pandas dataframe:

In [11]:
df = pd \
    .DataFrame.from_dict(counter, orient='index') \
    .sort_values(0, ascending=False) \
    .reset_index() \
    .rename(columns={'index':'word', 0:'count'})

df.index = df.index + 1

df.head()

word  count
1  the  16083
2   of   6789
3  and   5885
4   in   5079
5   to   4786

Compute the proportion that each word appear inside the corpus:

In [12]:
df['proportion'] = df['count']/df['count'].sum()
df.head()

word  count  proportion
1  the  16083    0.082016
2   of   6789    0.034621
3  and   5885    0.030011
4   in   5079    0.025901
5   to   4786    0.024407

Compute number of tokens and vocab size of the corpus:

In [13]:
vocab_size, _ = df.shape
n_tokens = df['count'].sum()

print(f'Vocabulary size: {vocab_size:>8,}\nNumber of tokens: {n_tokens:,}')

Vocabulary size:   17,733
Number of tokens: 196,095


Compute the predicted proprotion using classic [zipf's law](https://en.wikipedia.org/wiki/Zipf%27s_law):

In [14]:
def classic_zipf(N, k, s=1):
    return (1/k**s)/(np.sum(1/(np.arange(1, N+1)**s)))

# view some samples
N = n_tokens

for i in range(0, 3):
    print(f'N={N:,}, k={10**i:<3}: {classic_zipf(N, 10**i):.4f}')

N=196,095, k=1  : 0.0783
N=196,095, k=10 : 0.0078
N=196,095, k=100: 0.0008


In [15]:
%%time
vectorize_classic_zipf = np.vectorize(lambda x: classic_zipf(N, x))

df['predicted_proportion'] = vectorize_classic_zipf(df.index.values)

CPU times: user 20.6 s, sys: 32.4 ms, total: 20.6 s
Wall time: 20.6 s


In [16]:
df.head()

word  count  proportion  predicted_proportion
1  the  16083    0.082016              0.078348
2   of   6789    0.034621              0.039174
3  and   5885    0.030011              0.026116
4   in   5079    0.025901              0.019587
5   to   4786    0.024407              0.015670

View the 10 most common and least common words:

In [17]:
df.head(10)

word  count  proportion  predicted_proportion
1    the  16083    0.082016              0.078348
2     of   6789    0.034621              0.039174
3    and   5885    0.030011              0.026116
4     in   5079    0.025901              0.019587
5     to   4786    0.024407              0.015670
6      a   4031    0.020556              0.013058
7    was   2575    0.013131              0.011193
8     on   1903    0.009704              0.009793
9     as   1605    0.008185              0.008705
10  that   1522    0.007762              0.007835

In [18]:
df.tail(10)

word  count  proportion  predicted_proportion
17724     pomelaa      1    0.000005              0.000004
17725     morisil      1    0.000005              0.000004
17726  comprising      1    0.000005              0.000004
17727      claire      1    0.000005              0.000004
17728      shrill      1    0.000005              0.000004
17729       sleep      1    0.000005              0.000004
17730     bottles      1    0.000005              0.000004
17731       bowen      1    0.000005              0.000004
17732     hutchin      1    0.000005              0.000004
17733      pelkey      1    0.000005              0.000004

# Visualization

log-log plot using the predicted proportion:

In [19]:
x = np.log(df.index.values)
y = np.log(df['predicted_proportion'] * n_tokens)

trace = go.Scatter(
    x = x,
    y = y,
    mode = 'markers'
)

layout = go.Layout(
    xaxis = {
        'title': 'log(rank of word i)'
    },
    yaxis = {
        'title': 'log(count of word i)'
    }
)
data = [trace]
fig = go.Figure(data=data, layout=layout)

# Plot and embed in ipython notebook!
py.iplot(fig)

Combine the actual and expected log-log plot:

In [20]:
x = np.log(df.index.values)
y = np.log(df['count'])

trace1 = go.Scatter(
    x = x,
    y = y,
    mode = 'markers',
    name = 'emprical'
)

x = np.log(df.index.values)
y = np.log(df['predicted_proportion'] * n_tokens)

trace2 = go.Scatter(
    x = x,
    y = y,
    mode = 'markers',
    name = 'theoretical'
)

data = [trace1, trace2]
fig = go.Figure(data=data, layout=layout)
py.iplot(fig)

# Statistical Tests

Do a chi-square test to see if data follows a classic zipf distribution:

In [21]:
df['expected_count'] = df['predicted_proportion'] * n_tokens

# scipy documentation on chisquare says:
# A typical rule is that all of the observed and expected frequencies should be at least 5.
df_chi = df[['count', 'expected_count']].query('expected_count > 5 and count > 5')
df_chi.describe()

count  expected_count
count   3072.000000     3072.000000
mean      53.523763       43.047525
std      378.055998      352.921164
min        8.000000        5.001187
25%       11.000000        6.667525
50%       17.000000        9.999119
75%       32.000000       19.985236
max    16083.000000    15363.644973

In [22]:
actual_count = df_chi['count']
expected_count = df_chi['expected_count']

In [23]:
test_stat, p_value = scipy.stats.chisquare(actual_count, expected_count)
print(f'test statistic value: {test_stat:,.4f}')
print(f'p-value: {p_value: > 24}')
print(f'p-value < 0.05: {"yes" if p_value < 5/100 else "no":>17}')

test statistic value: 17,744.1274
p-value:                      0.0
p-value < 0.05:               yes
